In [ ]:
# required packages: geopandas & plotly
# For plotly, simply use 
# conda 
# installing geopands on windows can be tricky, see below for a solution

In [1]:
import re 
import pandas as pd 
import numpy as np
pd.options.display.max_rows = 100

# plotting
import plotly.express as px
import plotly.figure_factory as ff

## Installation guide: geopandas

There are two steps:

1. download packages from: https://www.lfd.uci.edu/~gohlke/pythonlibs/

We need 1) GDAL; 2) pyproj; 3)Fiona; 4) Shapely; and 5) geopandas

Get the correct version. For example, with python 3.8.x on a x64 OS, we need GDAL‑3.1.4‑cp38‑cp38‑win_amd64.whl

2. install the packages

open cmd (anaconda), and cd to the folder with these packages
`cd/d F:\DataMining\geopandas`

install packages (you only need to type: pip install xx and use tab to autofill the file names)
`pip install GDAL-3.1.4-cp38-cp38-win_amd64.whl
pip install pyproj-3.0.0.post1-cp38-cp38-win_amd64.whl
pip install Fiona-1.8.18-cp38-cp38-win_amd64.whl
pip install Shapely-1.7.1-cp38-cp38-win_amd64.whl
pip install geopandas-0.8.1-py3-none-any.whl`

# main data for empirical application

Input: `HPI.csv`, `macro.csv` and `FRM30.csv`

Output: `empirical_main.csv`

In [2]:
# read HPI
hpi = pd.read_csv('F:/Research/GLP/data/HPI.csv')
# transform wide to long
hpi = hpi.melt(id_vars='Month')
hpi.columns = ['date','MSA','HPI']

# read macro.csv
macro = pd.read_csv('F:/Research/GLP/data/macro.csv',skiprows=[1])
macro = macro.iloc[:,0:-3]

# read FRM30.csv, convert it to monthly data
frm = pd.read_csv('F:/Research/GLP/data/FRM30.csv')
frm.date = frm.date.apply(lambda x: x.split('/')[0]+'M'+x.split('/')[1].zfill(2))
frm = frm.groupby('date').mean().reset_index()

# merge
df = pd.merge(hpi,macro,how='outer',on='date')
df = df.merge(frm,how='left',on='date')
df['date'] = pd.to_datetime(df.date,format='%YM%m')
df = df.sort_values(['MSA','date']).reset_index(drop=True)

In [3]:
# local economic conditions: unemployment rate
SID = pd.read_csv('F:/Research/GLP/data/raw/la.area.txt', sep='\t', header='infer')
SID = SID.iloc[:,[1,2]]
SID.columns = ['SID','MSA']

UR = pd.read_excel('F:/Research/GLP/data/raw/SeriesReport-20210215212313_4378ec.xlsx')
UR.columns = UR.iloc[2,:]
UR = UR.iloc[3:,:]
UR['Series ID'] = UR['Series ID'].apply(lambda x: x[3:-2])
UR = UR.rename(columns={'Series ID':'SID'})
UR = UR.merge(SID,how='left',on=['SID'])
UR = UR.iloc[:,1:].melt(id_vars=['MSA'])
UR.columns = ['MSA','date','UR']
UR.date = pd.to_datetime(UR.date)

# make MSA names consistent
# simple rules
UR.MSA = UR.MSA.str.replace(r'\s*Metropolitan Statistical Area\s*','',regex=True)
UR.MSA = UR.MSA.str.replace(r'\s*Metropolitan NECTA\s*','',regex=True)

# approximation
MSA_rule = { 
             'Boston-Cambridge-Nashua, MA-NH':'Boston-Cambridge-Newton, MA-NH',
             'Manchester, NH':'Manchester-Nashua, NH',
             'Macon-Bibb County, GA': 'Macon, GA',
             'Norwich-New London-Westerly, CT-RI':'Norwich-New London, CT',
             'New Haven, CT':'New Haven-Milford, CT',
             'Springfield, MA-CT':'Springfield, MA'
            }

for key in MSA_rule:
    UR.loc[UR.MSA==key,'MSA'] = MSA_rule[key]

df = df.merge(UR,how='left',on=['date','MSA'])

In [4]:
df['INFL_H'] = pd.concat([df.loc[:,['date','MSA']],np.log(df.HPI)],axis=1).groupby('MSA').HPI.diff()*100
df['GRPI'] = pd.concat([df.loc[:,['date','MSA']],np.log(df.RPI)],axis=1).groupby('MSA').RPI.diff()*100
df['GIP'] = pd.concat([df.loc[:,['date','MSA']],np.log(df.INDPRO)],axis=1).groupby('MSA').INDPRO.diff()*100
df['GHOUST'] = pd.concat([df.loc[:,['date','MSA']],np.log(df.HOUST)],axis=1).groupby('MSA').HOUST.diff()*100
df['GPERMIT'] = pd.concat([df.loc[:,['date','MSA']],np.log(df.PERMIT)],axis=1).groupby('MSA').PERMIT.diff()*100
df['GREALLN'] = pd.concat([df.loc[:,['date','MSA']],np.log(df.REALLN)],axis=1).groupby('MSA').REALLN.diff()*100
df['INFL_CPI'] = pd.concat([df.loc[:,['date','MSA']],np.log(df.CPIAUCSL)],axis=1).groupby('MSA').CPIAUCSL.diff()*100
df['INFL_PCE'] = pd.concat([df.loc[:,['date','MSA']],np.log(df.PCEPI)],axis=1).groupby('MSA').PCEPI.diff()*100

In [5]:
df.to_csv('F:/Research/GLP/data/empirical_main.csv',index=False)

# MSA features

## Getting MSA_list

### Get Gr_EST from GLP

There are four possibilities

In [126]:
# change sheet name when needed
MSA_list = pd.read_excel('F:/Research/GLP/data/Gr_EST.xlsx',sheet_name='FE_Y')
MSA_list.columns = ['MSA','G2','G3','G4']
MSA_list.head()

MSA  G2  G3  G4
0                  Abilene, TX   2   3   4
1                    Akron, OH   2   3   3
2                   Albany, GA   2   3   4
3                   Albany, OR   1   2   2
4  Albany-Schenectady-Troy, NY   1   1   1

## Merging Economic Profile

In [127]:
MSA_rule = {'Albany-Lebanon, OR' : 'Albany, OR',
            'Anniston-Oxford-Jacksonville, AL' : 'Anniston-Oxford, AL',
            'Atlanta-Sandy Springs-Roswell, GA' : 'Atlanta-Sandy Springs-Alpharetta, GA',
            'Austin-Round Rock, TX' : 'Austin-Round Rock-Georgetown, TX',
            'Bend-Redmond, OR' : 'Bend, OR',
            'Blacksburg-Christiansburg-Radford, VA' :  'Blacksburg-Christiansburg, VA',
            'Bremerton-Silverdale, WA' : 'Bremerton-Silverdale-Port Orchard, WA',
            'Buffalo-Cheektowaga-Niagara Falls, NY' : 'Buffalo-Cheektowaga, NY',
            'Dayton-Kettering, OH' :  'Dayton, OH',
            'Eugene, OR' : 'Eugene-Springfield, OR',
            'Fayetteville-Springdale-Rogers, AR-MO' : 'Fayetteville-Springdale-Rogers, AR',
            'Grand Rapids-Wyoming, MI' :  'Grand Rapids-Kentwood, MI',
            'Greenville-Anderson-Mauldin, SC' :  'Greenville-Anderson, SC',
            'Gulfport-Biloxi-Pascagoula, MS' :  'Gulfport-Biloxi, MS',
            'Eugene, OR' : 'Eugene-Springfield, OR',
            'Grand Rapids-Wyoming, MI' :  'Grand Rapids-Kentwood, MI',
            'Greenville-Anderson-Mauldin, SC' :  'Greenville-Anderson, SC',
            'Gulfport-Biloxi-Pascagoula, MS' :  'Gulfport-Biloxi, MS',
            'Hilton Head Island-Bluffton-Beaufort, SC' : 'Hilton Head Island-Bluffton, SC',
            'Hartford-West Hartford-East Hartford, CT':'Hartford-East Hartford-Middletown, CT',
            'Kingsport-Bristol-Bristol, TN-VA' : 'Kingsport-Bristol, TN-VA',
            'Mankato-North Mankato, MN' :  'Mankato, MN',
            'Macon, GA':'Macon-Bibb County, GA',
            'Miami-Fort Lauderdale-West Palm Beach, FL' : 'Miami-Fort Lauderdale-Pompano Beach, FL',
            'Milwaukee-Waukesha-West Allis, WI' : 'Milwaukee-Waukesha, WI',
            'Naples-Immokalee-Marco Island, FL' : 'Naples-Marco Island, FL',
            'Niles-Benton Harbor, MI' : 'Niles, MI',
            'Olympia-Tumwater, WA' :  'Olympia-Lacey-Tumwater, WA',
            'Prescott, AZ' :  'Prescott Valley-Prescott, AZ',
            'Phoenix-Mesa-Scottsdale, AZ':'Phoenix-Mesa-Chandler, AZ',
            'Raleigh-Cary, NC' :  'Raleigh, NC',
            'Sacramento--Roseville--Arden-Arcade, CA' :  'Sacramento-Roseville-Folsom, CA',
            'San Diego-Carlsbad, CA' :  'San Diego-Chula Vista-Carlsbad, CA',
            'San Francisco-Oakland-Hayward, CA' :  'San Francisco-Oakland-Berkeley, CA',
            'San Luis Obispo-Paso Robles-Arroyo Grande, CA' :  'San Luis Obispo-Paso Robles, CA',
            'Santa Rosa, CA' :   'Santa Rosa-Petaluma, CA',
            'Scranton--Wilkes-Barre, PA' : 'Scranton--Wilkes-Barre--Hazleton, PA',
            'Sebring, FL' :  'Sebring-Avon Park, FL',
            'Staunton-Waynesboro, VA' : 'Staunton, VA',
            'Stockton-Lodi, CA' : 'Stockton, CA',
            'Trenton, NJ' : 'Trenton-Princeton, NJ',
            'Vallejo-Fairfield, CA' :  'Vallejo, CA',
            'Visalia-Porterville, CA' : 'Visalia, CA',
            'Wausau, WI' : 'Wausau-Weston, WI'}

In [128]:
# read profile
prof = pd.read_csv('F:/Research/GLP/data/EconProfile_MSA.csv')
prof = prof.pivot(index='GeoName', columns='Description',values='2017').reset_index()

# clean MSA names
prof['GeoName'] = prof.GeoName.str.replace(r'\s\(.*\).*','',regex=True)

# read gdp (thousands of chained 2012 dollars)
gdp = pd.read_csv('F:/Research/GLP/data/GDP_MSA.csv')
gdp['GeoName'] = gdp.GeoName.str.replace(r'\s\(.*\).*','',regex=True)

# merge
prof = pd.merge(prof,gdp,how='outer',on='GeoName',indicator=True)
prof[prof._merge!='both']
prof = prof.drop(columns='_merge') # drop merge indicators

# rename columns
prof.columns = ['MSA','PINCPC','POP','PINC','EMP','cbsa','RGDP'] 
prof['RGDPPC'] = prof['RGDP']/prof['POP']*1000                            # create real gdp per capita

In [129]:
prof['POP'] = prof['POP']/1000
prof['EMP'] = prof['EMP']/1000

In [130]:
# debt to income ratio
debt = pd.read_csv('F:/Research/GLP/data/household-debt-by-msa.csv')
debt = debt.groupby(['Year','Metropolitan Statistical Areas']).mean().reset_index().iloc[:,[1,3,4]]
debt.columns = ['MSA', 'D2I_Low','D2I_H']
debt['MSA'] = debt.MSA.str.replace(r'\s\(.*\).*','',regex=True)

In [131]:
# change MSA names to match Sep 2018 record
for key in MSA_rule:
    prof.loc[prof.MSA==key,'MSA'] = MSA_rule[key]
    debt.loc[debt.MSA==key,'MSA'] = MSA_rule[key]
    MSA_list.loc[MSA_list.MSA==key,'MSA'] = MSA_rule[key]

In [132]:
MSA_list = pd.merge(MSA_list,prof,how='outer',on='MSA',indicator=True)
MSA_list[MSA_list._merge!='both']

MSA  G2  G3  G4  PINCPC      POP  \
382  Poughkeepsie-Newburgh-Middletown, NY NaN NaN NaN   51658  673.253   
383                        Twin Falls, ID NaN NaN NaN   37897  109.037   

         PINC      EMP   cbsa      RGDP        RGDPPC      _merge  
382  34779113  348.386  39100  27492574  40835.427395  right_only  
383   4132141   64.497  46300   4493510  41210.873373  right_only

In [133]:
MSA_list = MSA_list[MSA_list._merge!='right_only']
MSA_list = MSA_list.drop(columns='_merge')
MSA_list = pd.merge(MSA_list,debt,how='outer',on='MSA',indicator=True)
MSA_list[MSA_list._merge!='both']

MSA   G2   G3   G4  PINCPC     POP     PINC     EMP   cbsa     RGDP  \
110  Enid, OK  1.0  2.0  2.0   42493  61.492  2612964  37.566  21420  3345503   

           RGDPPC  D2I_Low  D2I_H     _merge  
110  54405.499902      NaN    NaN  left_only

In [134]:
MSA_list = MSA_list[MSA_list._merge!='right_only']
MSA_list = MSA_list.drop(columns='_merge')

## Supply Elasticity & Regulation Index

In [135]:
MSA_rule2 = { 'Allentown-Bethlehem-Easton, PA': 'Allentown-Bethlehem-Easton, PA-NJ',
              'Appleton-Oshkosh-Neenah, WI': 'Appleton, WI',
              'Atlanta, GA': 'Atlanta-Sandy Springs-Alpharetta, GA',
              'Atlantic-Cape May, NJ': 'Atlantic City-Hammonton, NJ',
              'Augusta-Aiken, GA-SC' :'Augusta-Richmond County, GA-SC',
              'Austin-San Marcos, TX': 'Austin-Round Rock-Georgetown, TX',
              'Baltimore, MD': 'Baltimore-Columbia-Towson, MD',
              'Barnstable-Yarmouth, MA': 'Barnstable Town, MA',
              'Biloxi-Gulfport-Pascagoula, MS': 'Gulfport-Biloxi, MS',
              'Birmingham, AL': 'Birmingham-Hoover, AL',
              'Bloomington-Normal, IL': 'Bloomington, IL',
              'Boston-Worcester-Lawrence-Lowell-Brocktn, MA-NH': 'Boston-Cambridge-Newton, MA-NH',
              'Boulder-Longmont, CO': 'Boulder, CO',
              'Bremerton, WA': 'Bremerton-Silverdale-Port Orchard, WA',
              'Brownsville-Harlingen-San Benito, TX': 'Brownsville-Harlingen, TX',
              'Bryan-College Station, TX': 'College Station-Bryan, TX',
              'Buffalo-Niagara Falls, NY':'Buffalo-Cheektowaga, NY',
              'Burlington, VT': 'Burlington-South Burlington, VT',
              'Charlotte-Gastonia-Rock Hill, NC-SC': 'Charlotte-Concord-Gastonia, NC-SC',
              'Chicago, IL': 'Chicago-Naperville-Elgin, IL-IN-WI',
              'Chico-Paradise, CA': 'Chico, CA',
              'Cleveland-Lorain-Elyria, OH': 'Cleveland-Elyria, OH',
              'Dallas, TX': 'Dallas-Fort Worth-Arlington, TX',
              'Fort Worth-Arlington, TX':'Dallas-Fort Worth-Arlington, TX',
              'Dayton-Springfield, OH': 'Dayton, OH',
              'Daytona Beach, FL': 'Deltona-Daytona Beach-Ormond Beach, FL',
              'Denver, CO': 'Denver-Aurora-Lakewood, CO',
              'Des Moines, IA': 'Des Moines-West Des Moines, IA',
              'Detroit, MI': 'Detroit-Warren-Dearborn, MI',
              'Duluth-Superior, MN-WI': 'Duluth, MN-WI',
              'Evansville-Henderson, IN-KY': 'Evansville, IN-KY',
              'Fargo-Moorhead, ND-MN': 'Fargo, ND-MN',
              'Flagstaff, AZ-UT': 'Flagstaff, AZ',
              'Fort Collins-Loveland, CO': 'Fort Collins, CO',
              'Grand Rapids-Muskegon-Holland, MI': 'Grand Rapids-Kentwood, MI',
              'Greensboro-Winston-Salem-High Point, NC': 'Greensboro-High Point, NC',
              'Greenville-Spartanburg-Anderson, SC': 'Greenville-Anderson, SC',
              'Hagerstown, MD': 'Hagerstown-Martinsburg, MD-WV',
              'Harrisburg-Lebanon-Carlisle, PA': 'Harrisburg-Carlisle, PA',
              'Hartford, CT': 'Hartford-East Hartford-Middletown, CT',
              'Hickory-Morganton-Lenoir, NC': 'Hickory-Lenoir-Morganton, NC',
              'Houston, TX': 'Houston-The Woodlands-Sugar Land, TX',
              'Galveston-Texas City, TX': 'Houston-The Woodlands-Sugar Land, TX',
              'Indianapolis, IN': 'Indianapolis-Carmel-Anderson, IN',
              'Johnson City-Kingsport-Bristol, TN-VA': 'Johnson City, TN',
              'Kalamazoo-Battle Creek, MI': 'Kalamazoo-Portage, MI',
              'La Crosse, WI-MN': 'La Crosse-Onalaska, WI-MN',
              'Lafayette, IN': 'Lafayette-West Lafayette, IN',
              'Las Vegas, NV-AZ': 'Las Vegas-Henderson-Paradise, NV',
              'Lexington, KY': 'Lexington-Fayette, KY',
              'Little Rock-North Little Rock, AR': 'Little Rock-North Little Rock-Conway, AR',
              'Longview-Marshall, TX': 'Longview, TX',
              'Los Angeles-Long Beach, CA': 'Los Angeles-Long Beach-Anaheim, CA',
              'Louisville, KY-IN': 'Louisville/Jefferson County, KY-IN',
              'Medford-Ashland, OR': 'Medford, OR',
              'Memphis, TN-AR-MS': 'Memphis, TN-MS-AR',
              'Minneapolis-St. Paul, MN-WI': 'Minneapolis-St. Paul-Bloomington, MN-WI',
              'Myrtle Beach, SC': 'Myrtle Beach-Conway-North Myrtle Beach, SC-NC',
              'Naples, FL': 'Naples-Marco Island, FL',
              'Nashville, TN': 'Nashville-Davidson--Murfreesboro--Franklin, TN',
              'New Haven-Bridgprt-Stamfrd-Danbry-Wtrbry, CT': 'New Haven-Milford, CT',
              'New London-Norwich, CT': 'Norwich-New London, CT',
              'New Orleans, LA': 'New Orleans-Metairie, LA',
              'Olympia, WA': 'Olympia-Lacey-Tumwater, WA',
              'Omaha, NE-IA': 'Omaha-Council Bluffs, NE-IA',
              'Orlando, FL': 'Orlando-Kissimmee-Sanford, FL',
              'Parkersburg-Marietta, WV-OH': 'Parkersburg-Vienna, WV',
              'Pensacola, FL': 'Pensacola-Ferry Pass-Brent, FL',
              'Peoria-Pekin, IL': 'Peoria, IL',
              'Philadelphia, PA-NJ': 'Philadelphia-Camden-Wilmington, PA-NJ-DE-MD',
              'Phoenix-Mesa, AZ': 'Phoenix-Mesa-Chandler, AZ',
              'Portland, ME': 'Portland-South Portland, ME',
              'Portland-Vancouver, OR-WA': 'Portland-Vancouver-Hillsboro, OR-WA',
              'Providence-Warwick-Pawtucket, RI': 'Providence-Warwick, RI-MA',
              'Raleigh-Durham-Chapel Hill, NC': 'Raleigh, NC',
              'Richmond-Petersburg, VA': 'Richmond, VA',
              'Riverside-San Bernardino, CA': 'Riverside-San Bernardino-Ontario, CA',
              'Saginaw-Bay City-Midland, MI': 'Saginaw, MI',
              'St. Joseph, MO': 'St. Joseph, MO-KS',
              'Salt Lake City-Ogden, UT': 'Salt Lake City, UT',
              'San Antonio, TX': 'San Antonio-New Braunfels, TX',
              'San Diego, CA': 'San Diego-Chula Vista-Carlsbad, CA',
              'San Francisco, CA': 'San Francisco-Oakland-Berkeley, CA',
              'Oakland, CA': 'San Francisco-Oakland-Berkeley, CA',
              'San Jose, CA': 'San Jose-Sunnyvale-Santa Clara, CA',
              'San Luis Obispo-Atascadero-Paso Robles, CA': 'San Luis Obispo-Paso Robles, CA',
              'Santa Barbara-Santa Maria-Lompoc, CA': 'Santa Maria-Santa Barbara, CA',
              'Seattle-Bellevue-Everett, WA': 'Seattle-Tacoma-Bellevue, WA',
              'Sioux City, IA-NE': 'Sioux City, IA-NE-SD',
              'South Bend, IN': 'South Bend-Mishawaka, IN-MI',
              'Spokane, WA': 'Spokane-Spokane Valley, WA',
              'Texarkana, TX-Texarkana AR': 'Texarkana, TX-AR',
              'Vallejo-Fairfield-Napa, CA': 'Vallejo, CA',
              'Vineland-Millville-Bridgeton, NJ': 'Vineland-Bridgeton, NJ',
              'Washington, DC-MD-VA-WV': 'Washington-Arlington-Alexandria, DC-VA-MD-WV',
              'York, PA':'York-Hanover, PA',
              'Youngstown-Warren, OH': 'Youngstown-Warren-Boardman, OH-PA',
              'Fort Lauderdale, FL': 'Miami-Fort Lauderdale-Pompano Beach, FL',
              'Miami, FL':'Miami-Fort Lauderdale-Pompano Beach, FL',
              'Melbourne-Titusville-Palm Bay, FL':'Palm Bay-Melbourne-Titusville, FL',
              'Fort Myers-Cape Coral, FL':'Cape Coral-Fort Myers, FL',
              'Fort Pierce-Port St. Lucie, FL':'Port St. Lucie, FL',
              'Fort Walton Beach, FL': 'Crestview-Fort Walton Beach-Destin, FL',
              'New York, NY': 'New York-Newark-Jersey City, NY-NJ-PA',
              'Newark, NJ': 'New York-Newark-Jersey City, NY-NJ-PA',
              'Jersey City, NJ':'New York-Newark-Jersey City, NY-NJ-PA',
              'Norfolk-Virginia Beach-Newport News, VA-NC':'Virginia Beach-Norfolk-Newport News, VA-NC',
              'Richland-Kennewick-Pasco, WA': 'Kennewick-Richland, WA',
              'Sarasota-Bradenton, FL': 'North Port-Sarasota-Bradenton, FL',
              'Scranton-Wilkes-Barre-Hazleton, PA': 'Scranton--Wilkes-Barre--Hazleton, PA',
              'Steubenville-Weirton, OH-WV': 'Weirton-Steubenville, WV-OH',
              'Tacoma, WA': 'Seattle-Tacoma-Bellevue, WA',
              'Ventura, CA': 'Oxnard-Thousand Oaks-Ventura, CA',
              'Visalia-Tulare-Porterville, CA':'Visalia, CA',
              'West Palm Beach-Boca Raton, FL': 'Palm Bay-Melbourne-Titusville, FL',
              'Hamilton-Middletown, OH':'Cincinnati, OH-KY-IN',
              'Kenosha, WI':'Chicago-Naperville-Elgin, IL-IN-WI',
              'Sharon, PA':'Youngstown-Warren-Boardman, OH-PA',
              'Benton Harbor, MI':'Niles, MI'
}

In [136]:
supp = pd.read_stata('F:/Research/GLP/data/HOUSING_SUPPLY.dta')
supp = supp.rename(columns={'msaname':'MSA'})
supp['MSA'] = supp.MSA.str.replace(r'\s+\([A-Z]+\)','',regex=True)
supp = supp[['MSA','WRLURI','elasticity']]
for key in MSA_rule:
    supp.loc[supp.MSA==key,'MSA'] = MSA_rule[key]
for key in MSA_rule2:
    supp.loc[supp.MSA==key,'MSA'] = MSA_rule2[key]
    

In [137]:
supp = supp.groupby('MSA').mean().reset_index()

In [138]:
MSA_list = pd.merge(MSA_list,supp,how='outer',on='MSA',indicator=True)
MSA_list[MSA_list._merge=='right_only']

MSA  G2  G3  G4  PINCPC  POP  PINC  EMP  cbsa  RGDP  \
382                  Gary, IN NaN NaN NaN     NaN  NaN   NaN  NaN   NaN   NaN   
383             Jamestown, NY NaN NaN NaN     NaN  NaN   NaN  NaN   NaN   NaN   
384           Newburgh, NY-PA NaN NaN NaN     NaN  NaN   NaN  NaN   NaN   NaN   
385  Wilmington-Newark, DE-MD NaN NaN NaN     NaN  NaN   NaN  NaN   NaN   NaN   

     RGDPPC  D2I_Low  D2I_H    WRLURI  elasticity      _merge  
382     NaN      NaN    NaN -0.694470    1.736834  right_only  
383     NaN      NaN    NaN -0.648981    2.868494  right_only  
384     NaN      NaN    NaN -0.046225    1.787929  right_only  
385     NaN      NaN    NaN  0.467964    1.991168  right_only

In [139]:
MSA_list = MSA_list[MSA_list._merge!='right_only']
MSA_list = MSA_list.drop(columns='_merge')

## Generate Table 6 in the paper

### FE with lagged Y

In [37]:
# mean
g = 'G2'
base = MSA_list[[g,'RGDPPC','PINCPC','POP','EMP','WRLURI','elasticity','D2I_Low','D2I_H']].groupby(g).mean().reset_index()
for g in ['G3','G4']:
    base = pd.concat([base,MSA_list[[g,'RGDPPC','PINCPC','POP','EMP','WRLURI','elasticity','D2I_Low','D2I_H']].groupby(g).mean().reset_index()])
    
    
# standard deviation
g = 'G2'
base1 = MSA_list[[g,'RGDPPC','PINCPC','POP','EMP','WRLURI','elasticity','D2I_Low','D2I_H']].groupby(g).std().reset_index()
for g in ['G3','G4']:
    base1 = pd.concat([base1,MSA_list[[g,'RGDPPC','PINCPC','POP','EMP','WRLURI','elasticity','D2I_Low','D2I_H']].groupby(g).std().reset_index()])

count = MSA_list.groupby('G2')['MSA'].count().reset_index()
for g in ['G3','G4']:
    count = pd.concat([count,MSA_list[[g,'MSA']].groupby(g)['MSA'].count().reset_index()])

tab6 = pd.concat([base,base1,count['MSA']],axis=1)
tab6.iloc[:,[22,0,1,12,2,13,3,14,4,15,5,16,6,17,7,18,8,19,9,10]]

MSA   G2        RGDPPC        RGDPPC        PINCPC        PINCPC  \
0  163  1.0  50956.711345  17069.757496  48013.159509  11022.468242   
1  219  2.0  44121.295986  10832.704349  44356.607306   8912.516160   
0   50  NaN  54408.822840  18560.889158  50732.740000  13502.516707   
1  157  NaN  48463.184489  14837.613613  46052.605096   9032.607519   
2  175  NaN  43653.409505  10955.997096  44419.120000   9294.532538   
0   47  NaN  54723.492291  19051.057579  51165.191489  13738.944056   
1   91  NaN  48509.141479  11985.653041  46258.307692   7731.467124   
2  113  NaN  46786.619631  15444.457435  45573.000000  11372.427618   
3  131  NaN  43475.448394  11152.150573  44093.305344   7818.061411   

           POP          POP         EMP          EMP    WRLURI    WRLURI  \
0   979.041074  2256.486730  614.833380  1467.368738  0.048262  0.888173   
1   545.061489   893.459082  331.859900   583.578901 -0.253884  0.750411   
0  1088.719800  2144.285037  679.029280  1411.048421  0.408153  0.842105   
1   827.032172  2036.794650  522.175815  1325.473102 -0.229298  0.823549   
2   540.983543   863.858069  325.497669   550.620724 -0.193174  0.761297   
0  1121.848787  2206.411218  701.142979  1452.142404  0.466403  0.823250   
1   854.817967  2228.779560  534.659967  1441.947071 -0.074149  0.883590   
2   678.055115  1379.739864  426.611283   909.326023 -0.398789  0.689303   
3   548.218359   956.724468  328.857305   608.915753 -0.148952  0.776486   

   elasticity  elasticity   D2I_Low   D2I_Low     D2I_H     D2I_H   G3   G4  
0    2.293089    1.229462  1.438318  0.482511  1.574510  0.433164  NaN  NaN  
1    2.824563    1.559360  1.420993  0.486846  1.596528  0.471512  NaN  NaN  
0    1.702695    0.851441  1.621450  0.552621  1.771278  0.504865  1.0  NaN  
1    2.770184    1.264947  1.370929  0.418090  1.515447  0.386714  2.0  NaN  
2    2.714187    1.651270  1.424386  0.507088  1.602545  0.484873  3.0  NaN  
0    1.702017    0.875697  1.635426  0.549992  1.776012  0.494071  NaN  1.0  
1    2.423383    1.145111  1.389389  0.424162  1.505756  0.377977  NaN  2.0  
2    3.021933    1.639384  1.328341  0.432719  1.512905  0.399916  NaN  3.0  
3    2.696626    1.484417  1.467118  0.517420  1.645980  0.511118  NaN  4.0

Get rich and poor MSA list

In [38]:
print(MSA_list.PINCPC.describe(percentiles=[0.9]))
print(MSA_list.loc[MSA_list.G3==1,'PINCPC'].describe(percentiles=[0.1]))

count       382.000000
mean      45916.863874
std       10019.399870
min       25451.000000
50%       43932.500000
90%       56249.600000
max      112769.000000
Name: PINCPC, dtype: float64
count       50.000000
mean     50732.740000
std      13502.516707
min      30153.000000
10%      38424.000000
50%      46399.000000
max      98690.000000
Name: PINCPC, dtype: float64


In [41]:
MSA_list['PINCPC_90th'] = 0
MSA_list.loc[MSA_list.PINCPC>=56249.6,'PINCPC_90th']=1

In [42]:
MSA_list['PoorG3_1'] = 0
MSA_list.loc[(MSA_list.G3==1)&(MSA_list.PINCPC<=38424),'PoorG3_1'] = 1

In [43]:
MSA_list.to_csv('F:/Research/GLP/data/MSA_Feature_FE_Y.csv')

### FE without Y

In [69]:
# mean
g = 'G2'
base = MSA_list[[g,'RGDPPC','PINCPC','POP','EMP','WRLURI','elasticity','D2I_Low','D2I_H']].groupby(g).mean().reset_index()
for g in ['G3','G4']:
    base = pd.concat([base,MSA_list[[g,'RGDPPC','PINCPC','POP','EMP','WRLURI','elasticity','D2I_Low','D2I_H']].groupby(g).mean().reset_index()])
    
    
# standard deviation
g = 'G2'
base1 = MSA_list[[g,'RGDPPC','PINCPC','POP','EMP','WRLURI','elasticity','D2I_Low','D2I_H']].groupby(g).std().reset_index()
for g in ['G3','G4']:
    base1 = pd.concat([base1,MSA_list[[g,'RGDPPC','PINCPC','POP','EMP','WRLURI','elasticity','D2I_Low','D2I_H']].groupby(g).std().reset_index()])

count = MSA_list.groupby('G2')['MSA'].count().reset_index()
for g in ['G3','G4']:
    count = pd.concat([count,MSA_list[[g,'MSA']].groupby(g)['MSA'].count().reset_index()])

tab6 = pd.concat([base,base1,count['MSA']],axis=1)
tab6.iloc[:,[22,0,1,12,2,13,3,14,4,15,5,16,6,17,7,18,8,19,9,10]]

MSA   G2        RGDPPC        RGDPPC        PINCPC        PINCPC  \
0  162  1.0  49930.511996  17054.228475  47672.104938  11328.943446   
1  220  2.0  44908.021940  11301.411860  44624.368182   8737.106834   
0  134  NaN  50193.666568  18011.758675  48065.000000  11661.010925   
1  153  NaN  46969.975924  11564.032852  45457.379085   9133.537590   
2   95  NaN  42696.317198  10594.171076  43626.873684   8208.610954   
0  119  NaN  50472.740822  18812.564902  47898.075630  12204.298094   
1   89  NaN  48391.050672  11364.892422  46573.573034   7475.486162   
2   94  NaN  45134.110784  10991.523455  44818.319149  10089.026623   
3   80  NaN  42660.521110  10877.256305  43530.012500   8123.856381   

          POP          POP         EMP          EMP    WRLURI    WRLURI  \
0  881.631568  2131.814178  551.069265  1391.138442  0.086608  0.864275   
1  618.762941  1127.389327  380.099718   728.526486 -0.278980  0.761500   
0  785.803134  1585.559335  485.308075  1028.233501  0.157891  0.913228   
1  770.158765  1959.000441  490.328124  1286.585646 -0.344477  0.706506   
2  587.581579  1011.648297  345.722884   626.294661 -0.152924  0.772602   
0  754.928479  1585.976312  465.440849  1032.402136  0.154405  0.956355   
1  877.122348  2353.925481  556.240618  1527.613768 -0.306429  0.700338   
2  722.330266  1247.241022  452.936287   837.640976 -0.150175  0.800498   
3  539.409225  1021.829399  317.828400   633.756100 -0.266954  0.695620   

   elasticity  elasticity   D2I_Low   D2I_Low     D2I_H     D2I_H   G3   G4  
0    2.226844    1.001326  1.464550  0.476702  1.608709  0.445717  NaN  NaN  
1    2.867785    1.658670  1.401875  0.489418  1.571730  0.462564  NaN  NaN  
0    2.131226    1.019241  1.516353  0.489472  1.658360  0.454767  1.0  NaN  
1    2.848882    1.593629  1.366324  0.465230  1.525136  0.435310  2.0  NaN  
2    2.810271    1.559566  1.405079  0.494521  1.589973  0.477400  3.0  NaN  
0    2.180425    1.051613  1.528559  0.503342  1.663977  0.458297  NaN  1.0  
1    2.733683    1.424421  1.283708  0.449533  1.439331  0.387315  NaN  2.0  
2    2.554605    1.630561  1.456277  0.422556  1.625440  0.435746  NaN  3.0  
3    3.044285    1.595216  1.408687  0.527707  1.597825  0.511018  NaN  4.0

Get rich and poor MSA list

In [70]:
print(MSA_list.PINCPC.describe(percentiles=[0.9]))
print(MSA_list.loc[MSA_list.G3==1,'PINCPC'].describe(percentiles=[0.1]))

count       382.000000
mean      45916.863874
std       10019.399870
min       25451.000000
50%       43932.500000
90%       56249.600000
max      112769.000000
Name: PINCPC, dtype: float64
count       134.000000
mean      48065.000000
std       11661.010925
min       30153.000000
10%       37845.900000
50%       44523.000000
max      108595.000000
Name: PINCPC, dtype: float64


In [71]:
MSA_list['PINCPC_90th'] = 0
MSA_list.loc[MSA_list.PINCPC>=56249.6,'PINCPC_90th']=1

In [72]:
MSA_list['PoorG3_1'] = 0
MSA_list.loc[(MSA_list.G3==1)&(MSA_list.PINCPC<=37845.9),'PoorG3_1'] = 1

In [75]:
MSA_list.to_csv('F:/Research/GLP/data/MSA_Feature_FE_NoY.csv')

In [ ]:
# mean
g = 'G2'
base = MSA_list[[g,'RGDPPC','PINCPC','POP','EMP','WRLURI','elasticity','D2I_Low','D2I_H']].groupby(g).mean().reset_index()
for g in ['G3','G4']:
    base = pd.concat([base,MSA_list[[g,'RGDPPC','PINCPC','POP','EMP','WRLURI','elasticity','D2I_Low','D2I_H']].groupby(g).mean().reset_index()])
    
    
# standard deviation
g = 'G2'
base1 = MSA_list[[g,'RGDPPC','PINCPC','POP','EMP','WRLURI','elasticity','D2I_Low','D2I_H']].groupby(g).std().reset_index()
for g in ['G3','G4']:
    base1 = pd.concat([base1,MSA_list[[g,'RGDPPC','PINCPC','POP','EMP','WRLURI','elasticity','D2I_Low','D2I_H']].groupby(g).std().reset_index()])

count = MSA_list.groupby('G2')['MSA'].count().reset_index()
for g in ['G3','G4']:
    count = pd.concat([count,MSA_list[[g,'MSA']].groupby(g)['MSA'].count().reset_index()])

tab6 = pd.concat([base,base1,count['MSA']],axis=1)
tab6.iloc[:,[22,0,1,12,2,13,3,14,4,15,5,16,6,17,7,18,8,19,9,10]]

Get rich and poor MSA list

print(MSA_list.PINCPC.describe(percentiles=[0.9]))
print(MSA_list.loc[MSA_list.G3==1,'PINCPC'].describe(percentiles=[0.1]))

MSA_list['PINCPC_90th'] = 0
MSA_list.loc[MSA_list.PINCPC>=56249.6,'PINCPC_90th']=1

MSA_list['PoorG3_1'] = 0
MSA_list.loc[(MSA_list.G3==1)&(MSA_list.PINCPC<=37845.9),'PoorG3_1'] = 1

MSA_list.to_csv('F:/Research/GLP/data/MSA_Feature_FE_NoY.csv')

### RE With lagged Y

In [140]:
# mean
g = 'G2'
base = MSA_list[[g,'RGDPPC','PINCPC','POP','EMP','WRLURI','elasticity','D2I_Low','D2I_H']].groupby(g).mean().reset_index()
for g in ['G3','G4']:
    base = pd.concat([base,MSA_list[[g,'RGDPPC','PINCPC','POP','EMP','WRLURI','elasticity','D2I_Low','D2I_H']].groupby(g).mean().reset_index()])
    
    
# standard deviation
g = 'G2'
base1 = MSA_list[[g,'RGDPPC','PINCPC','POP','EMP','WRLURI','elasticity','D2I_Low','D2I_H']].groupby(g).std().reset_index()
for g in ['G3','G4']:
    base1 = pd.concat([base1,MSA_list[[g,'RGDPPC','PINCPC','POP','EMP','WRLURI','elasticity','D2I_Low','D2I_H']].groupby(g).std().reset_index()])

count = MSA_list.groupby('G2')['MSA'].count().reset_index()
for g in ['G3','G4']:
    count = pd.concat([count,MSA_list[[g,'MSA']].groupby(g)['MSA'].count().reset_index()])

tab6 = pd.concat([base,base1,count['MSA']],axis=1)
tab6.iloc[:,[22,0,1,12,2,13,3,14,4,15,5,16,6,17,7,18,8,19,9,10]]

MSA   G2        RGDPPC        RGDPPC        PINCPC        PINCPC  \
0  175  1.0  50826.615640  16592.828662  47861.782857  10736.861184   
1  207  2.0  43835.024315  10929.914006  44272.608696   9075.627076   
0   47  NaN  54738.847247  19039.489587  51013.744681  13871.860792   
1  137  NaN  49222.761343  15365.426662  46783.167883   9275.562315   
2  198  NaN  43698.301240  10738.499530  44107.585859   8933.883796   
0   46  NaN  55036.450061  19139.033261  51347.260870  13833.314181   
1  122  NaN  49502.643165  15638.534979  46722.172131   9298.269287   
2  131  NaN  44298.207851   9695.687586  44336.816794   9284.158097   
3   83  NaN  43306.546661  12606.273939  44217.349398   8530.803504   

           POP          POP         EMP          EMP    WRLURI    WRLURI  \
0   965.455109  2215.073204  609.601109  1444.561442 -0.019182  0.860057   
1   531.388971   838.619673  319.879058   537.360029 -0.217444  0.783555   
0  1124.414957  2205.495427  702.460511  1451.665111  0.459015  0.835399   
1   898.758708  2169.030312  569.891277  1411.331217 -0.218886  0.814806   
2   520.074318   821.514263  312.143485   523.482559 -0.209012  0.769844   
0  1139.881674  2227.287695  712.992609  1465.889440  0.501670  0.808349   
1   889.145926  2245.137559  565.745533  1464.369374 -0.189925  0.802367   
2   522.917870   691.707782  316.730435   435.797886 -0.373275  0.748404   
3   596.862169  1121.965426  356.444060   714.110168  0.014809  0.783805   

   elasticity  elasticity   D2I_Low   D2I_Low     D2I_H     D2I_H   G3   G4  
0    2.445580    1.199901  1.411925  0.475532  1.546818  0.423020  NaN  NaN  
1    2.728170    1.638133  1.442174  0.492538  1.620817  0.478898  NaN  NaN  
0    1.668060    0.855042  1.640904  0.545655  1.782083  0.488417  1.0  NaN  
1    2.835968    1.531544  1.327298  0.412641  1.469981  0.362145  2.0  NaN  
2    2.662217    1.416621  1.447323  0.498298  1.625697  0.485773  3.0  NaN  
0    1.669999    0.867822  1.647391  0.549849  1.789939  0.491791  NaN  1.0  
1    2.670218    1.148700  1.328719  0.426672  1.468632  0.373238  NaN  2.0  
2    2.990017    1.818312  1.361069  0.422362  1.548469  0.421204  NaN  3.0  
3    2.381720    1.156975  1.558434  0.553639  1.724643  0.534717  NaN  4.0

Get rich and poor MSA list

In [141]:
print(MSA_list.PINCPC.describe(percentiles=[0.9]))
print(MSA_list.loc[MSA_list.G3==1,'PINCPC'].describe(percentiles=[0.1]))

count       382.000000
mean      45916.863874
std       10019.399870
min       25451.000000
50%       43932.500000
90%       56249.600000
max      112769.000000
Name: PINCPC, dtype: float64
count       47.000000
mean     51013.744681
std      13871.860792
min      30153.000000
10%      38295.000000
50%      45476.000000
max      98690.000000
Name: PINCPC, dtype: float64


In [142]:
MSA_list['PINCPC_90th'] = 0
MSA_list.loc[MSA_list.PINCPC>=56249.6,'PINCPC_90th']=1

In [143]:
MSA_list['PoorG3_1'] = 0
MSA_list.loc[(MSA_list.G3==1)&(MSA_list.PINCPC<=38295),'PoorG3_1'] = 1

In [144]:
MSA_list.to_csv('F:/Research/GLP/data/MSA_Feature_RE_Y.csv')

### RE Without lagged Y

In [119]:
# mean
g = 'G2'
base = MSA_list[[g,'RGDPPC','PINCPC','POP','EMP','WRLURI','elasticity','D2I_Low','D2I_H']].groupby(g).mean().reset_index()
for g in ['G3','G4']:
    base = pd.concat([base,MSA_list[[g,'RGDPPC','PINCPC','POP','EMP','WRLURI','elasticity','D2I_Low','D2I_H']].groupby(g).mean().reset_index()])
    
    
# standard deviation
g = 'G2'
base1 = MSA_list[[g,'RGDPPC','PINCPC','POP','EMP','WRLURI','elasticity','D2I_Low','D2I_H']].groupby(g).std().reset_index()
for g in ['G3','G4']:
    base1 = pd.concat([base1,MSA_list[[g,'RGDPPC','PINCPC','POP','EMP','WRLURI','elasticity','D2I_Low','D2I_H']].groupby(g).std().reset_index()])

count = MSA_list.groupby('G2')['MSA'].count().reset_index()
for g in ['G3','G4']:
    count = pd.concat([count,MSA_list[[g,'MSA']].groupby(g)['MSA'].count().reset_index()])

tab6 = pd.concat([base,base1,count['MSA']],axis=1)
tab6.iloc[:,[22,0,1,12,2,13,3,14,4,15,5,16,6,17,7,18,8,19,9,10]]

MSA   G2        RGDPPC        RGDPPC        PINCPC        PINCPC  \
0  168  1.0  50484.425786  16801.599489  46912.160714  10391.904285   
1  214  2.0  44332.356253  11142.648703  45135.509346   9669.730879   
0  120  NaN  51276.068643  18355.074635  47455.183333  11240.401531   
1  149  NaN  45866.529622  10153.356024  44702.040268   7714.721982   
2  113  NaN  44082.005480  12836.242777  45885.097345  11140.433323   
0   85  NaN  50750.547746  16045.366189  47291.905882  10790.954991   
1  114  NaN  48820.057937  15917.622787  45829.894737   9463.048711   
2  107  NaN  44860.918891   9854.000649  44669.392523   8278.704430   
3   76  NaN  43277.714285  13409.352096  46265.750000  11969.567373   

          POP          POP         EMP          EMP    WRLURI    WRLURI  \
0  718.998107  1478.276777  449.855327   966.736906 -0.075899  0.780496   
1  739.067659  1748.909386  454.763850  1135.145512 -0.157682  0.863139   
0  709.786250  1545.154166  438.184750   994.280324 -0.031841  0.778846   
1  623.860235  1214.848461  389.285477   799.152563 -0.316253  0.860744   
2  892.235717  2132.323121  551.411088  1390.824153  0.019366  0.798700   
0  729.725424  1730.446258  459.241800  1129.558738  0.021858  0.799921   
1  734.653070  1340.927079  455.706886   871.937711 -0.235716  0.932836   
2  728.066159  2068.924563  453.066813  1343.557316 -0.325475  0.639440   
3  727.262776  1200.195044  439.879895   783.920204  0.162804  0.818526   

   elasticity  elasticity   D2I_Low   D2I_Low     D2I_H     D2I_H   G3   G4  
0    2.523314    1.217207  1.364656  0.467178  1.524177  0.418869  NaN  NaN  
1    2.645560    1.611745  1.478072  0.492882  1.637315  0.477356  NaN  NaN  
0    2.423625    1.078271  1.375378  0.475105  1.525197  0.415121  1.0  NaN  
1    2.895117    1.729911  1.367836  0.457762  1.540034  0.437076  2.0  NaN  
2    2.403421    1.374475  1.563960  0.505113  1.719905  0.496711  3.0  NaN  
0    2.415109    1.107186  1.438185  0.464334  1.598333  0.445993  NaN  1.0  
1    2.770664    1.802866  1.312632  0.470809  1.479000  0.407836  NaN  2.0  
2    2.849907    1.317311  1.349650  0.428095  1.521643  0.418063  NaN  3.0  
3    2.169538    1.255431  1.701908  0.502364  1.850588  0.497230  NaN  4.0

Get rich and poor MSA list

In [120]:
print(MSA_list.PINCPC.describe(percentiles=[0.9]))
print(MSA_list.loc[MSA_list.G3==1,'PINCPC'].describe(percentiles=[0.1]))

count       382.000000
mean      45916.863874
std       10019.399870
min       25451.000000
50%       43932.500000
90%       56249.600000
max      112769.000000
Name: PINCPC, dtype: float64
count       120.000000
mean      47455.183333
std       11240.401531
min       30153.000000
10%       38009.700000
50%       44780.000000
max      108595.000000
Name: PINCPC, dtype: float64


In [121]:
MSA_list['PINCPC_90th'] = 0
MSA_list.loc[MSA_list.PINCPC>=56249.6,'PINCPC_90th']=1

In [122]:
MSA_list['PoorG3_1'] = 0
MSA_list.loc[(MSA_list.G3==1)&(MSA_list.PINCPC<=38009),'PoorG3_1'] = 1

In [123]:
MSA_list.to_csv('F:/Research/GLP/data/MSA_Feature_RE_NoY.csv')

# Plot

## Group Evolution

In [4]:
# change sheet name when needed
MSA_list = pd.read_excel('F:/Research/GLP/data/Gr_EST.xlsx',sheet_name='FE_Y')
MSA_list.columns = ['MSA','G2','G3','G4','G5']
MSA_list.head()

MSA  G2  G3  G4  G5
0                  Abilene, TX   2   3   4   5
1                    Akron, OH   2   3   4   4
2                   Albany, GA   2   3   4   5
3                   Albany, OR   1   2   3   3
4  Albany-Schenectady-Troy, NY   1   1   1   1

In [8]:
fig = px.parallel_categories(MSA_list, dimensions=['G2', 'G3', 'G4'],
                color="G4", color_continuous_scale=px.colors.sequential.Inferno,
                labels={'G2':'G=2', 'G3':'G=3','G4':'G=4'})
fig.show()

In [7]:
fig = px.parallel_categories(MSA_list, dimensions=['G2', 'G3', 'G4','G5'],
                color="G4", color_continuous_scale=px.colors.sequential.Inferno,
                labels={'G2':'G=2', 'G3':'G=3','G4':'G=4','G5':'G=5'})
fig.show()

## Map

__First convert MSA to County__

According to [Freddie Mac](http://www.freddiemac.com/research/indices/fmhpi-faq.page), the definition of MSAs follow the most recent ones in Office of Management and Budget (OMB).

I take the Sep. 2018 one on their [website](https://www.census.gov/geographies/reference-files/time-series/demo/metro-micro/delineation-files.html)



__Details of codes and requirements are [here](https://plot.ly/python/county-choropleth/)__

### FE with lagged dependent variables

In [145]:
# load crosswalk
cross = pd.read_csv('F:/Research/GLP/data/cbsa_county.csv')
cross['FIPS'] = cross.apply(lambda x: str(x['FIPS State Code']).zfill(2)+str(x['FIPS County Code']).zfill(3), axis = 1) 
cross = cross.iloc[:,[0,1,6]]
cross.columns = ['cbsa','MSA','FIPS']

# load MSA feature
MSA_list.cbsa = MSA_list.cbsa.astype(int)

# merge data
cross = pd.merge(cross,MSA_list.iloc[:,[0,1,2,3,8]],how='outer',on='cbsa',indicator=True)

# keep only 382 MSAs used
cross = cross[cross._merge=='both']
cross = cross.drop(columns='_merge')

In [146]:
# plot mappings for G3 G4 using FIPS
# colorscale = ["#f7fbff","#ebf3fb","#deebf7","#d2e3f3","#c6dbef","#b3d2e9","#9ecae1",
#               "#85bcdb","#6baed6","#57a0ce","#4292c6","#3082be","#2171b5","#1361a9",
#               "#08519c","#0b4083","#08306b"]

colorscale = ["#08306b","#3082be","#c6dbef"]

fips = cross['FIPS'].tolist()
values = cross['G3'].astype(int).tolist()

fig = ff.create_choropleth(
    fips=fips, values=values,
    colorscale=colorscale,
    show_hover=True, 
    centroid_marker={'opacity': 0},
    asp=2.9,
    state_outline={'color': 'rgb(0,0,0)', 'width': 0.5},
    county_outline={'color': 'rgb(255,255,255)', 'width': 0.5},
)

fig.layout.template = None
fig.show()


In [51]:
# plot mappings for G3 G4 using FIPS
# colorscale = ["#f7fbff","#ebf3fb","#deebf7","#d2e3f3","#c6dbef","#b3d2e9","#9ecae1",
#               "#85bcdb","#6baed6","#57a0ce","#4292c6","#3082be","#2171b5","#1361a9",
#               "#08519c","#0b4083","#08306b"]

colorscale = ["#08306b","#3082be","#85bcdb","#c6dbef"]

fips = cross['FIPS'].tolist()
values = cross['G4'].astype(int).tolist()

fig = ff.create_choropleth(
    fips=fips, values=values,
    colorscale=colorscale,
    show_hover=True, 
    centroid_marker={'opacity': 0},
    asp=2.9,
    state_outline={'color': 'rgb(0,0,0)', 'width': 0.5},
    county_outline={'color': 'rgb(255,255,255)', 'width': 0.5},
)

fig.layout.template = None
fig.show()
